In [7]:
import tensorflow as tf
from tensorflow import keras
import numpy as np
from random import sample
import matplotlib.pyplot as plt
import os
import cv2
from keras import layers
from keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam
from proglearn.deciders import SimpleArgmaxAverage
from proglearn.progressive_learner import ProgressiveLearner
from proglearn.transformers import (
    NeuralClassificationTransformer,
    TreeClassificationTransformer,
)
from proglearn.voters import TreeClassificationVoter, KNNClassificationVoter
from sklearn.model_selection import train_test_split
from keras.backend import clear_session 
import pandas as pd
import pickle

In [2]:
TRAIN_DATADIR = '/Users/jayantadey/Downloads/LargeFineFoodAI/train'
VAL_DATADIR = '/Users/jayantadey/Downloads/LargeFineFoodAI/Val'

CATEGORIES = list(range(10))
SAMPLE_PER_CLASS = 60
NUM_CLASS_PER_TASK = 10
IMG_SIZE = 50

In [3]:
train_X = []
train_y = []
test_X = []
test_y = []
for category in CATEGORIES:
    path = os.path.join(TRAIN_DATADIR, str(category))
    
    images = os.listdir(path)
    total_images = len(images)
    train_indx = sample(range(total_images), SAMPLE_PER_CLASS)
    test_indx = np.delete(range(total_images), train_indx)
    for ii in train_indx:
        image_data = cv2.imread(
                os.path.join(path, images[ii])
            )
        resized_image = cv2.resize(
            image_data, 
            (IMG_SIZE, IMG_SIZE)
        )
        train_X.append(
            resized_image
        )
        train_y.append(
            category
        )
    for ii in test_indx:
        image_data = cv2.imread(
                os.path.join(path, images[ii])
            )
        resized_image = cv2.resize(
            image_data, 
            (IMG_SIZE, IMG_SIZE)
        )
        test_X.append(
            resized_image
        )
        test_y.append(
            category
        )

train_X = np.array(train_X).reshape(-1,IMG_SIZE,IMG_SIZE,3)
train_y = np.array(train_y)
test_X = np.array(test_X).reshape(-1,IMG_SIZE,IMG_SIZE,3)
test_y = np.array(test_y)

In [86]:
model='synn'
default_transformer_class = NeuralClassificationTransformer

network = keras.Sequential()
network.add(
    layers.Conv2D(
        filters=16,
        kernel_size=(3, 3),
        activation="relu",
        input_shape=np.shape(train_X[0]),
    )
)
network.add(layers.BatchNormalization())
network.add(
    layers.Conv2D(
        filters=32,
        kernel_size=(3, 3),
        strides=2,
        padding="same",
        activation="relu",
    )
)
network.add(layers.BatchNormalization())
network.add(
    layers.Conv2D(
        filters=64,
        kernel_size=(3, 3),
        strides=2,
        padding="same",
        activation="relu",
    )
)
network.add(layers.BatchNormalization())
network.add(
    layers.Conv2D(
        filters=128,
        kernel_size=(3, 3),
        strides=2,
        padding="same",
        activation="relu",
    )
)
network.add(layers.BatchNormalization())
network.add(
    layers.Conv2D(
        filters=254,
        kernel_size=(3, 3),
        strides=2,
        padding="same",
        activation="relu",
    )
)

network.add(layers.Flatten())
network.add(layers.BatchNormalization())
network.add(layers.Dense(2000, activation="relu"))
network.add(layers.BatchNormalization())
network.add(layers.Dense(2000, activation="relu"))
network.add(layers.BatchNormalization())
network.add(layers.Dense(units=10, activation="softmax")) 

default_transformer_kwargs = {
    "network": network,
    "euclidean_layer_idx": -2,
    "loss": "categorical_crossentropy",
    "optimizer": Adam(3e-4),
    "fit_kwargs": {
        "epochs": 200,
        "callbacks": [EarlyStopping(patience=5, monitor="val_loss")],
        "verbose": False,
        "validation_split": 0.33,
        "batch_size": 32,
    },
}
default_voter_class = KNNClassificationVoter
default_voter_kwargs = {"k": int(np.log2(500))}
default_decider_class = SimpleArgmaxAverage

progressive_learner = ProgressiveLearner(
        default_transformer_class=default_transformer_class,
        default_transformer_kwargs=default_transformer_kwargs,
        default_voter_class=default_voter_class,
        default_voter_kwargs=default_voter_kwargs,
        default_decider_class=default_decider_class,
    )

In [87]:
progressive_learner.add_task(
            X=train_X,
            y=train_y,
            task_id=0,
            num_transformers=1 if model == "synn" else ntrees,
            transformer_voter_decider_split=[0.67, 0.33, 0],
            decider_kwargs={"classes": np.unique(train_y)},
        )

2023-02-12 12:55:08.664036: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.
2023-02-12 12:55:09.963924: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


 1/11 [=>............................] - ETA: 1s

2023-02-12 12:55:17.734393: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


11/11 [==============================] - 0s 10ms/step


In [88]:
np.mean(progressive_learner.predict(
            X=test_X, transformer_ids=[0], task_id=0
        ) == test_y)

41/41 [==============================] - 0s 5ms/step


0.2562929061784897

In [4]:
def get_data(task=0):
    train_X = []
    train_y = []
    test_X = []
    test_y = []
    
    categories_to_consider = range(task*10,(task+1)*10)
    for category in categories_to_consider:
        path = os.path.join(TRAIN_DATADIR, str(category))

        images = os.listdir(path)
        total_images = len(images)
        train_indx = sample(range(total_images), SAMPLE_PER_CLASS)
        test_indx = np.delete(range(total_images), train_indx)
        for ii in train_indx:
            image_data = cv2.imread(
                    os.path.join(path, images[ii])
                )
            resized_image = cv2.resize(
                image_data, 
                (IMG_SIZE, IMG_SIZE)
            )
            train_X.append(
                resized_image
            )
            train_y.append(
                category
            )
        for ii in test_indx:
            image_data = cv2.imread(
                    os.path.join(path, images[ii])
                )
            resized_image = cv2.resize(
                image_data, 
                (IMG_SIZE, IMG_SIZE)
            )
            test_X.append(
                resized_image
            )
            test_y.append(
                category
            )

    train_X = np.array(train_X).reshape(-1,IMG_SIZE,IMG_SIZE,3)
    train_y = np.array(train_y)
    test_X = np.array(test_X).reshape(-1,IMG_SIZE,IMG_SIZE,3)
    test_y = np.array(test_y)
    
    return train_X, train_y, test_X, test_y

In [8]:
def experiment(model='synf', ntrees=10, rep=1):
    num_tasks = 100
    tasks = []
    base_tasks = []
    accuracies_across_tasks = []
    singletask_accuracy = []
    df_multitask = pd.DataFrame()
    df_singletask = pd.DataFrame()

    if model == "synn":

        clear_session()  # clear GPU memory before each run, to avoid OOM error

        default_transformer_class = NeuralClassificationTransformer

        network = keras.Sequential()
        network.add(
            layers.Conv2D(
                filters=16,
                kernel_size=(3, 3),
                activation="relu",
                input_shape=(IMG_SIZE,IMG_SIZE,3),
            )
        )
        network.add(layers.BatchNormalization())
        network.add(
            layers.Conv2D(
                filters=32,
                kernel_size=(3, 3),
                strides=2,
                padding="same",
                activation="relu",
            )
        )
        network.add(layers.BatchNormalization())
        network.add(
            layers.Conv2D(
                filters=64,
                kernel_size=(3, 3),
                strides=2,
                padding="same",
                activation="relu",
            )
        )
        network.add(layers.BatchNormalization())
        network.add(
            layers.Conv2D(
                filters=128,
                kernel_size=(3, 3),
                strides=2,
                padding="same",
                activation="relu",
            )
        )
        network.add(layers.BatchNormalization())
        network.add(
            layers.Conv2D(
                filters=254,
                kernel_size=(3, 3),
                strides=2,
                padding="same",
                activation="relu",
            )
        )

        network.add(layers.Flatten())
        network.add(layers.BatchNormalization())
        network.add(layers.Dense(2000, activation="relu"))
        network.add(layers.BatchNormalization())
        network.add(layers.Dense(2000, activation="relu"))
        network.add(layers.BatchNormalization())
        network.add(layers.Dense(units=NUM_CLASS_PER_TASK, activation="softmax"))  # units=10

        default_transformer_kwargs = {
            "network": network,
            "euclidean_layer_idx": -2,
            "loss": "categorical_crossentropy",
            "optimizer": Adam(3e-4),
            "fit_kwargs": {
                "epochs": 100,
                "callbacks": [EarlyStopping(patience=5, monitor="val_loss")],
                "verbose": False,
                "validation_split": 0.33,
                "batch_size": 32,
            },
        }
        default_voter_class = KNNClassificationVoter
        default_voter_kwargs = {"k": int(np.log2(500))}
        default_decider_class = SimpleArgmaxAverage

    elif model == "synf":

        default_transformer_class = TreeClassificationTransformer
        default_transformer_kwargs = {"kwargs": {"max_depth": 30}}
        default_voter_class = TreeClassificationVoter
        default_voter_kwargs = {}
        default_decider_class = SimpleArgmaxAverage

    progressive_learner = ProgressiveLearner(
        default_transformer_class=default_transformer_class,
        default_transformer_kwargs=default_transformer_kwargs,
        default_voter_class=default_voter_class,
        default_voter_kwargs=default_voter_kwargs,
        default_decider_class=default_decider_class,
    )
    
    test_x_task = []
    test_y_task = []
    for task in range(num_tasks):
        print("doing task ", task)
        
        train_x, train_y, test_x, test_y = get_data(task)
        train_x = train_x.reshape(-1, 3*IMG_SIZE*IMG_SIZE)
        test_x = test_x.reshape(-1, 3*IMG_SIZE*IMG_SIZE)
        
        test_x_task.append(
            test_x
        )
        test_y_task.append(
            test_y
        )
        progressive_learner.add_task(
            X=train_x,
            y=train_y,
            task_id=task,
            num_transformers=1 if model == "synn" else ntrees,
            transformer_voter_decider_split=[0.67, 0.33, 0],
            decider_kwargs={"classes": np.unique(train_y)},
        )

        singletask_prediction = progressive_learner.predict(
            X=test_x, transformer_ids=[task], task_id=task
        )
        singletask_accuracy.append(
            np.mean(singletask_prediction==test_y)
        )
        print('accuracy ',np.mean(singletask_prediction==test_y))
        for ii in range(task+1):
            multitask_prediction = progressive_learner.predict(
                X=test_x_task[ii], task_id=ii
            )
            acc = np.mean(multitask_prediction==test_y_task[ii])
            print('task ',ii,' accuracy ', acc)
            base_tasks.append(task+1)
            tasks.append(ii+1)
            accuracies_across_tasks.append(
                np.mean(multitask_prediction == test_y_task[ii])
            )

    df_multitask['task'] = tasks
    df_multitask['base_task'] = base_tasks
    df_multitask['accuracy'] = accuracies_across_tasks

    df_singletask['task'] = list(range(1,num_tasks+1))
    df_singletask['accuracy'] = singletask_accuracy

    summary = (df_multitask, df_singletask)

    with open('results/'+model+'_'+str(rep)+'.pickle', 'wb') as f:
        pickle.dump(summary, f)


In [ ]:
reps = 1

for ii in range(reps):
    experiment(model='synn',rep=ii)

doing task  0


2023-02-12 16:56:23.815248: W tensorflow/core/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz
2023-02-12 16:56:24.119645: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.
2023-02-12 16:56:26.687944: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


1/7 [===>..........................] - ETA: 0s

2023-02-12 16:56:32.835393: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


54/54 [==============================] - 0s 4ms/step
accuracy  0.19871420222092342
54/54 [==============================] - 0s 6ms/step
task  0  accuracy  0.19871420222092342
doing task  1


...

71/71 [==============================] - 1s 17ms/step
accuracy  0.3417665335108744
54/54 [==============================] - 1s 12ms/step


54/54 [==============================] - 2s 30ms/step
task  0  accuracy  0.44535359438924604
55/55 [==============================] - 2s 34ms/step
task  1  accuracy  0.5069044879171462
77/77 [==============================] - 1s 9ms/step


77/77 [==============================] - 1s 18ms/step
task  2  accuracy  0.4713114754098361
70/70 [==============================] - 1s 19ms/step
task  3  accuracy  0.507815989280929
96/96 [==============================] - 1s 8ms/step


96/96 [==============================] - 2s 16ms/step
task  4  accuracy  0.6189542483660131
71/71 [==============================] - 2s 33ms/step
task  5  accuracy  0.5425297487880123
100/100 [==============================] - 1s 5ms/step


100/100 [==============================] - 1s 14ms/step
task  6  accuracy  0.5525657071339174
70/70 [==============================] - 1s 8ms/step
task  7  accuracy  0.6101922217255252
100/113 [=========================>....] - ETA: 0s

In [9]:
reps = 1

for ii in range(reps):
    experiment(model='synf',rep=ii)

doing task  0
accuracy  0.3185271770894214
task  0  accuracy  0.3185271770894214
doing task  1
accuracy  0.4085155350978136
task  0  accuracy  0.33664523670368207
task  1  accuracy  0.4315304948216341
doing task  2
accuracy  0.3463114754098361
task  0  accuracy  0.34658094681472823
task  1  accuracy  0.43498273878020716
task  2  accuracy  0.36926229508196723
doing task  3
accuracy  0.38276016078606523
task  0  accuracy  0.364114552893045
task  1  accuracy  0.4441887226697353
task  2  accuracy  0.3930327868852459
task  3  accuracy  0.42206342117016526
doing task  4
accuracy  0.4493464052287582
task  0  accuracy  0.3489187609585038
task  1  accuracy  0.452819332566168
task  2  accuracy  0.39467213114754096
task  3  accuracy  0.41447074586869137
task  4  accuracy  0.5
doing task  5
accuracy  0.4142794182459233
task  0  accuracy  0.3617767387492694
task  1  accuracy  0.45569620253164556
task  2  accuracy  0.39795081967213114
task  3  accuracy  0.42340330504689594
task  4  accuracy  0.51013

task  2  accuracy  0.4487704918032787
task  3  accuracy  0.4582402858418937
task  4  accuracy  0.5620915032679739
task  5  accuracy  0.4944909651829
task  6  accuracy  0.44242803504380473
task  7  accuracy  0.5359856951274028
task  8  accuracy  0.4923632324354346
task  9  accuracy  0.4621276595744681
task  10  accuracy  0.48711943793911006
task  11  accuracy  0.3669305724725944
task  12  accuracy  0.31970260223048325
task  13  accuracy  0.4795288839035334
task  14  accuracy  0.51338199513382
task  15  accuracy  0.3696369636963696
task  16  accuracy  0.35875
task  17  accuracy  0.4920328343795268
task  18  accuracy  0.5832632464255677
task  19  accuracy  0.5871156661786238
doing task  20
accuracy  0.3695652173913043
task  0  accuracy  0.4172998246639392
task  1  accuracy  0.476409666283084
task  2  accuracy  0.4471311475409836
task  3  accuracy  0.456900401965163
task  4  accuracy  0.5647058823529412
task  5  accuracy  0.49052446011458795
task  6  accuracy  0.4405506883604506
task  7  a

task  19  accuracy  0.5973645680819912
task  20  accuracy  0.47132284921369105
task  21  accuracy  0.5093194625054183
task  22  accuracy  0.48880597014925375
task  23  accuracy  0.5053507728894173
task  24  accuracy  0.5492246664262531
task  25  accuracy  0.5005988023952096
task  26  accuracy  0.5392303848075962
task  27  accuracy  0.4729647630619684
doing task  28
accuracy  0.37741808132649035
task  0  accuracy  0.42489772063120984
task  1  accuracy  0.4700805523590334
task  2  accuracy  0.45286885245901637
task  3  accuracy  0.4546672621706119
task  4  accuracy  0.5784313725490197
task  5  accuracy  0.49228735125605994
task  6  accuracy  0.45369211514392993
task  7  accuracy  0.5288332588287885
task  8  accuracy  0.48930852540960845
task  9  accuracy  0.46
task  10  accuracy  0.4894613583138173
task  11  accuracy  0.36479902557856275
task  12  accuracy  0.31055190162996854
task  13  accuracy  0.47784632641615254
task  14  accuracy  0.5194647201946472
task  15  accuracy  0.36680810938

task  7  accuracy  0.5333035315154224
task  8  accuracy  0.49291863371285755
task  9  accuracy  0.4702127659574468
task  10  accuracy  0.4894613583138173
task  11  accuracy  0.36084043848964675
task  12  accuracy  0.3128395767800972
task  13  accuracy  0.47448121144139094
task  14  accuracy  0.5164233576642335
task  15  accuracy  0.36916548797736914
task  16  accuracy  0.3528125
task  17  accuracy  0.509415741187832
task  18  accuracy  0.5950378469301935
task  19  accuracy  0.5949243533430942
task  20  accuracy  0.47548566142460685
task  21  accuracy  0.49718248807975723
task  22  accuracy  0.4925373134328358
task  23  accuracy  0.5049544193420531
task  24  accuracy  0.5503065272268302
task  25  accuracy  0.5037924151696607
task  26  accuracy  0.5412293853073463
task  27  accuracy  0.4665856622114216
task  28  accuracy  0.43426766679826295
task  29  accuracy  0.4553692795650204
task  30  accuracy  0.4570552147239264
task  31  accuracy  0.4878140232470941
task  32  accuracy  0.479299363

task  29  accuracy  0.4553692795650204
task  30  accuracy  0.4565439672801636
task  31  accuracy  0.48556430446194226
task  32  accuracy  0.4781050955414013
task  33  accuracy  0.5543206446235065
task  34  accuracy  0.579527048914804
task  35  accuracy  0.396964389959136
task  36  accuracy  0.5622435020519836
task  37  accuracy  0.46256239600665555
task  38  accuracy  0.4312977099236641
task  39  accuracy  0.4466414655423088
doing task  40
accuracy  0.4055186866922808
task  0  accuracy  0.4289888953828171
task  1  accuracy  0.4798619102416571
task  2  accuracy  0.46762295081967215
task  3  accuracy  0.4609200535953551
task  4  accuracy  0.5875816993464053
task  5  accuracy  0.4839136183340679
task  6  accuracy  0.45369211514392993
task  7  accuracy  0.5364327223960662
task  8  accuracy  0.49375173562899194
task  9  accuracy  0.474468085106383
task  10  accuracy  0.49121779859484777
task  11  accuracy  0.3690621193666261
task  12  accuracy  0.31541321132399197
task  13  accuracy  0.4711

...

task  39  accuracy  0.4504216341959872
task  40  accuracy  0.5047153335661894
task  41  accuracy  0.607497243660419
task  42  accuracy  0.38597194388777556
task  43  accuracy  0.49971313826735514
task  44  accuracy  0.47658656808379546
task  45  accuracy  0.5201581027667984
task  46  accuracy  0.41450068399452805
task  47  accuracy  0.46138002059732236
task  48  accuracy  0.3883309421329507
task  49  accuracy  0.44728761514841353
task  50  accuracy  0.4560683760683761
task  51  accuracy  0.3385719166381961
task  52  accuracy  0.5434782608695652
task  53  accuracy  0.42836041358936483
task  54  accuracy  0.5851688693098385
task  55  accuracy  0.5172203596464493
task  56  accuracy  0.38644688644688646
task  57  accuracy  0.5876637093367132
task  58  accuracy  0.38282387190684136
task  59  accuracy  0.5394868377207598
task  60  accuracy  0.6970643347907558
task  61  accuracy  0.4992107340173639
task  62  accuracy  0.4174609226077011
task  63  accuracy  0.46663321625689913
task  64  accura

task  64  accuracy  0.42885611797528894
task  65  accuracy  0.5219224283305227
task  66  accuracy  0.6131031429836211
task  67  accuracy  0.41769474797321116
task  68  accuracy  0.5179889298892989
task  69  accuracy  0.5671588044652502
task  70  accuracy  0.49844651575676874
task  71  accuracy  0.5955334987593052
task  72  accuracy  0.3686892079666512
task  73  accuracy  0.4481106971793507
task  74  accuracy  0.5453431372549019
task  75  accuracy  0.5062034739454094
task  76  accuracy  0.41989708404802745
task  77  accuracy  0.5716530483972344
task  78  accuracy  0.5293238700037355
task  79  accuracy  0.5503184713375796
task  80  accuracy  0.4688181421718273
task  81  accuracy  0.5265822784810127
task  82  accuracy  0.5169890224777836
task  83  accuracy  0.4462809917355372
task  84  accuracy  0.474181174387725
task  85  accuracy  0.5396825396825397
task  86  accuracy  0.4635078333970195
task  87  accuracy  0.5494949494949495
task  88  accuracy  0.47283702213279677
task  89  accuracy  0

task  86  accuracy  0.4631257164692396
task  87  accuracy  0.5523232323232323
task  88  accuracy  0.47456165564817476
task  89  accuracy  0.5106167846309403
task  90  accuracy  0.47587548638132293
task  91  accuracy  0.536318407960199
task  92  accuracy  0.5091774303195106
task  93  accuracy  0.48636859323882226
task  94  accuracy  0.4742005813953488
doing task  95
accuracy  0.40831600831600834
task  0  accuracy  0.43658679135008766
task  1  accuracy  0.48791714614499426
task  2  accuracy  0.4713114754098361
task  3  accuracy  0.47833854399285397
task  4  accuracy  0.6098039215686275
task  5  accuracy  0.4892022917584839
task  6  accuracy  0.4571339173967459
task  7  accuracy  0.5391148860080465
task  8  accuracy  0.4940294362677034
task  9  accuracy  0.48638297872340425
task  10  accuracy  0.4953161592505855
task  11  accuracy  0.3766747868453106
task  12  accuracy  0.3151272519302259
task  13  accuracy  0.4991587212563096
task  14  accuracy  0.5164233576642335
task  15  accuracy  0.3

task  5  accuracy  0.4883208461877479
task  6  accuracy  0.4596370463078849
task  7  accuracy  0.5395619132767099
task  8  accuracy  0.4898639266870314
task  9  accuracy  0.485531914893617
task  10  accuracy  0.4953161592505855
task  11  accuracy  0.37728380024360536
task  12  accuracy  0.31426937374892766
task  13  accuracy  0.49803701626472235
task  14  accuracy  0.5164233576642335
task  15  accuracy  0.3851956624233852
task  16  accuracy  0.365
task  17  accuracy  0.5161757605021728
task  18  accuracy  0.5946173254835997
task  19  accuracy  0.5978526110297706
task  20  accuracy  0.47964847363552265
task  21  accuracy  0.49978326831382747
task  22  accuracy  0.5051305970149254
task  23  accuracy  0.5108997225525168
task  24  accuracy  0.5557158312297151
task  25  accuracy  0.5157684630738523
task  26  accuracy  0.5357321339330335
task  27  accuracy  0.46780072904009723
task  28  accuracy  0.451243584682195
task  29  accuracy  0.4680561848663344
task  30  accuracy  0.467280163599182
t

task  16  accuracy  0.3665625
task  17  accuracy  0.5200386286817963
task  18  accuracy  0.592094196804037
task  19  accuracy  0.5988286969253295
task  20  accuracy  0.4805735430157262
task  21  accuracy  0.5006501950585176
task  22  accuracy  0.5046641791044776
task  23  accuracy  0.5112960760998811
task  24  accuracy  0.5571583122971511
task  25  accuracy  0.5161676646706587
task  26  accuracy  0.5317341329335332
task  27  accuracy  0.46354799513973266
task  28  accuracy  0.45084879589419663
task  29  accuracy  0.46986859990937924
task  30  accuracy  0.4662576687116564
task  31  accuracy  0.500562429696288
task  32  accuracy  0.491640127388535
task  33  accuracy  0.5643234231731037
task  34  accuracy  0.5834143181081957
task  35  accuracy  0.4028021015761821
task  36  accuracy  0.5728454172366622
task  37  accuracy  0.46630615640599
task  38  accuracy  0.43765903307888043
task  39  accuracy  0.44838615876708343
task  40  accuracy  0.5036674816625917
task  41  accuracy  0.606945975744